## Imports

### General Imports

In [1]:
import pandas as pd
import numpy as np
import os
import joblib

In [55]:
from sklearn.model_selection import train_test_split
from sklearn.datasets import load_iris
from sklearn.ensemble import AdaBoostClassifier

### Imports for checks

In [3]:
import mlchecks
from mlchecks.base import Dataset

In [66]:
from mlchecks.checks.overview import dataset_info, model_info

from mlchecks.checks.integrity import mixed_nulls
from mlchecks.checks.integrity.is_single_value import is_single_value
from mlchecks.checks import string_mismatch
from mlchecks.checks.leakage import DataSampleLeakageReport, data_sample_leakage_report

from mlchecks.checks import IndexTrainValidationLeakage, index_train_validation_leakage
from mlchecks.checks.integrity.rare_format_detection import RareFormatDetection, rare_format_detection

from mlchecks.checks.performance import ClassificationReport, ConfusionMatrixReport
from mlchecks.checks.overfit import train_validation_difference_overfit

from mlchecks.checks.integrity.dataset_drift import dataset_drift

## Lending Club

### Load Data & Model

In [60]:
LENDINGCLUB_DATASET_BASEDIR = os.path.join('datasets', 'Lending Club')
KKBOX_DATASET_BASEDIR = os.path.join('datasets', 'kkbox')

os.listdir(LENDINGCLUB_DATASET_BASEDIR)

['model.joblib', 'Roles.docx', 'test.csv', 'train.csv']

In [61]:
df_train = pd.read_csv(os.path.join(LENDINGCLUB_DATASET_BASEDIR, 'train.csv'))
df_train.issue_d = pd.to_datetime(df_train.issue_d)
df_val = pd.read_csv(os.path.join(LENDINGCLUB_DATASET_BASEDIR, 'test.csv'))
df_val.issue_d = pd.to_datetime(df_val.issue_d)
lending_club_model = joblib.load(os.path.join(LENDINGCLUB_DATASET_BASEDIR, 'model.joblib'))

#### Define Metadata for Dataset

In [49]:
# dataset metadata (manaul)

categorical_features = ['addr_state',
 'application_type',
 'disbursement_method',
 'grade',
 'home_ownership',
 'initial_list_status',
 'purpose',
 'term',
 'verification_status']

all_features = ['sub_grade', 'term', 'home_ownership', 'fico_range_low',
       'total_acc', 'pub_rec', 'revol_util', 'annual_inc', 'int_rate', 'dti',
       'purpose', 'mort_acc', 'loan_amnt', 'application_type', 'installment',
       'verification_status', 'pub_rec_bankruptcies', 'addr_state',
       'initial_list_status', 'fico_range_high', 'revol_bal', 'open_acc',
       'emp_length', 'time_to_earliest_cr_line']

label_col_name = 'loan_status'
index_col_name = 'id'
date_col_name = 'issue_d'
# label_name_dict = {0: "Default", 1: "OK"}

In [50]:
ds_train = Dataset(df_train, cat_features = categorical_features, features=all_features,
                   label = label_col_name, index = index_col_name, date=date_col_name)
ds_val = Dataset(df_val, cat_features = categorical_features, features=all_features,
                   label = label_col_name, index = index_col_name, date=date_col_name)

### Additional for showing validation faults


#### demo util function

In [9]:
def dataset_from_dict(d: dict, index_name: str = None) -> Dataset:
    dataframe = pd.DataFrame(data=d)
    return Dataset(dataframe, index=index_name)

#### demo data

In [10]:
# mixed nulls
mixed_nulls_demo_data = {'col1': ['nan', None, 'null', 'Nan', '1', 'cat'], 'col2':['', '', 'None', 'a', 'b', 'c'], 'col3': [1,2,3,4,5,6]}
df_mixed_nulls = pd.DataFrame(data=mixed_nulls_demo_data)

In [11]:
# single value
df_single_value_demo = pd.DataFrame({'a':[3,4,1], 'b':[2,2,2], 'c':[None, None, None], 'd':['a', 4, 6]})

In [12]:
# synthetic index leakage
train_df_synthetic_leakage = dataset_from_dict({'col1': [1, 2, 3, 4, 10, 11]}, 'col1')
val_df_synthetic_leakage = dataset_from_dict({'col1': [4, 3, 5, 6, 7]}, 'col1')

In [13]:
# string mismatch data
data = {'col1': ['Deep', 'deep', 'deep!!!', '$deeP$', 'earth', 'foo', 'bar', 'foo?']}
df_string_mismatch = pd.DataFrame(data=data)

In [14]:
# index leakage
iris = load_iris(as_frame=True)
frame = iris.frame
X = iris.data
y = iris.target
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=55)
train_ds_index_leakage = Dataset(pd.concat([X_train, y_train], axis=1), 
            features=iris.feature_names,
            label='target')

test_df = pd.concat([X_test, y_test], axis=1)
bad_test = test_df.append(train_ds_index_leakage.iloc[[0, 1, 2, 3, 4]], ignore_index=True)
                    
val_ds_index_leakage = Dataset(bad_test, 
            features=iris.feature_names,
            label='target')

In [15]:
# rare format detection
df = pd.DataFrame(np.random.choice(a=['BIG', 'STILL_BIG'], size=(200,3)), columns=['x1', 'x2', 'x3'])
df = df.append({'x1': 'bla', 'x2': 'BIG', 'x3': 1}, ignore_index=True)
df = df.append({'x1': 'bla', 'x2': 'BIG', 'x3': 1}, ignore_index=True)
rare_format_df = df.append({'x1': 'bla2', 'x2': 'BIG', 'x3': 2}, ignore_index=True)

In [56]:
# overfit check
overfit_clf = AdaBoostClassifier()
iris = load_iris(as_frame=True)
frame = iris.frame
X = iris.data
Y = iris.target
X_train, X_test, y_train, y_test = train_test_split(
            X, Y, test_size=0.33, random_state=42)
overfit_train_ds = Dataset(pd.concat([X_train, y_train], axis=1), 
            features=iris.feature_names,
            label='target')
overfit_val_ds = Dataset(pd.concat([X_test, y_test], axis=1), 
            features=iris.feature_names,
            label='target')
overfit_clf.fit(X_train, y_train)

AdaBoostClassifier()

##### Drift demo data

In [71]:
df = pd.read_csv(os.path.join(KKBOX_DATASET_BASEDIR, 'train_clean.csv'))
test_df = pd.read_csv(os.path.join(KKBOX_DATASET_BASEDIR, 'test_clean.csv'))

In [72]:
test_df.date = pd.to_datetime(test_df.date*10**9)

In [73]:
drift_org_dataset = Dataset(test_df,  
                 features=['num_25', 'num_50', 'num_75', 'num_985', 'num_100', 'num_unq',
       'total_secs', 'days_listened', 'plan_list_price', 'is_auto_renew',
       'is_cancel', 'gender', 'registered_via', 'secs_per_song', 'num_days'],
                  label='y_true49a0c676-35fd-11ea-978f-2e728ce88125',
                  cat_features= ['gender', 'registered_via'],
                  index='msno', date='date')

drift_compared_dataset = Dataset(df,
                          features=['num_25', 'num_50', 'num_75', 'num_985', 'num_100', 'num_unq',
       'total_secs', 'days_listened', 'plan_list_price', 'is_auto_renew',
       'is_cancel', 'gender', 'registered_via', 'secs_per_song', 'num_days'],
                          label='y_true49a0c676-35fd-11ea-978f-2e728ce88125',
                          cat_features= ['gender', 'registered_via'],
                          index='msno')

## Run checks

### Overview

#### Dataset Info

In [16]:
dataset_info(ds_train)

Summarize dataset:   0%|          | 0/35 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

(260580, 27)

#### Model Info

In [17]:
model_info(lending_club_model)

{'type': 'CatBoostClassifier', 'params': {'iterations': 50, 'learning_rate': 0.10014066482404328, 'depth': 7, 'l2_leaf_reg': 4.247331314864416, 'random_seed': 0, 'auto_class_weights': 'Balanced', 'eval_metric': 'AUC', 'allow_writing_files': False, 'cat_features': ['sub_grade', 'term', 'home_ownership', 'purpose', 'application_type', 'verification_status', 'addr_state', 'initial_list_status']}}

### Integrity

#### Mixed Nulls

In [18]:
mixed_nulls(df_mixed_nulls)

Count  Fraction of data
Column Name Value                         
col1        nan        1              0.06
            NaN        1              0.06
            null       1              0.06
            Nan        1              0.06
col2                   2              0.11
            None       1              0.06

In [19]:
mixed_nulls(df_train)

Empty DataFrame
Columns: [Count, Fraction of data]
Index: []

In [20]:
mixed_nulls(df_val)

Empty DataFrame
Columns: [Count, Fraction of data]
Index: []

#### Single Value

In [21]:
is_single_value(df_single_value_demo)

True

In [22]:
is_single_value(df_train)

False

In [23]:
is_single_value(df_val)

False

#### String Mismatch

In [76]:
string_mismatch(df_string_mismatch)

Value  Count  Fraction of data
Column Name Base form                                  
col1        deep          deep      1              0.12
            deep        $deeP$      1              0.12
            deep       deep!!!      1              0.12
            deep          Deep      1              0.12
            foo            foo      1              0.12
            foo           foo?      1              0.12

In [77]:
string_mismatch(df_train)

Empty DataFrame
Columns: [Value, Count, Fraction of data]
Index: []

In [28]:
string_mismatch(df_val)

Empty DataFrame
Columns: [Value, Count, Fraction of data]
Index: []

#### Rare Format Detection

In [78]:
rare_format_detection(rare_format_df)
# rare_format_df = df.append({'x1': 'bla2', 'x2': 'BIG', 'x3': 2}, ignore_index=True)

{'x1':                                           digits only format (ignoring letters)  \
ratio of rare patterns to common patterns                                 1.06%   
common formats                                                              [_]   
examples for values in common formats                               [STILL_BIG]   
values in rare formats                                                   [bla2]   

                                          digits and letters format  \
ratio of rare patterns to common patterns                     0.50%   
common formats                                     [XXX, XXXXX_XXX]   
examples for values in common formats              [BIG, STILL_BIG]   
values in rare formats                                       [bla2]   

                                          digits and letters format (case sensitive)  \
ratio of rare patterns to common patterns                                      1.50%   
common formats                                                      [XXX, XXXXX_XXX]   
examples for values in common formats                               [BIG, STILL_BIG]   
values in rare formats                                                   [bla, bla2]   

                                          any sequence format  
ratio of rare patterns to common patterns               0.50%  
common formats                                 [SEQ, SEQ_SEQ]  
examples for values in common formats        [BIG, STILL_BIG]  
values in rare formats                                 [bla2]  , 'x2': Empty DataFrame
Columns: []
Index: [], 'x3':                                           digits only format (ignoring letters)  \
ratio of rare patterns to common patterns                                 3.06%   
common formats                                                              [_]   
examples for values in common formats                               [STILL_BIG]   
values in rare formats                                                   [1, 2]   

                                          digits and letters format  \
ratio of rare patterns to common patterns                     1.50%   
common formats                                     [XXX, XXXXX_XXX]   
examples for values in common formats              [BIG, STILL_BIG]   
values in rare formats                                       [1, 2]   

                                          digits and letters format (case sensitive)  \
ratio of rare patterns to common patterns                                      1.50%   
common formats                                                      [XXX, XXXXX_XXX]   
examples for values in common formats                               [BIG, STILL_BIG]   
values in rare formats                                                        [1, 2]   

                                          any sequence format  
ratio of rare patterns to common patterns               1.50%  
common formats                                 [SEQ, SEQ_SEQ]  
examples for values in common formats        [BIG, STILL_BIG]  
values in rare formats                                 [1, 2]  }

In [52]:
# rare_format_detection(df_train)

### Overfit

In [58]:
# train_validation_difference_overfit(overfit_train_ds, overfit_val_ds, overfit_clf)

In [79]:
train_validation_difference_overfit(ds_train, ds_val, lending_club_model)

More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).


{'Accuracy': -0.036625100255721965, 'Precision': -0.0548830601506094, 'Recall': -0.0470239716279609}

### Drift

In [80]:
dataset_drift(drift_org_dataset, drift_compared_dataset,over_time=True)

{'num_50': date
2019-10-06    0.001483
2019-11-10    0.004587
2019-12-08    0.005310
2020-01-05    0.006822
2020-02-09    0.010519
2020-03-08    0.012000
2020-04-05    0.009705
2020-05-10    0.015629
2020-05-24    0.015649
2020-06-07    0.016645
2020-06-21    0.017029
dtype: float64, 'num_25': date
2019-10-06    0.002231
2019-11-10    0.005429
2019-12-08    0.006727
2020-01-05    0.011342
2020-02-09    0.013151
2020-03-08    0.015210
2020-04-05    0.012710
2020-05-10    0.015110
2020-05-24    0.017102
2020-06-07    0.016609
2020-06-21    0.020746
dtype: float64, 'num_75': date
2019-10-06    0.001652
2019-11-10    0.005006
2019-12-08    0.005657
2020-01-05    0.004490
2020-02-09    0.011487
2020-03-08    0.013033
2020-04-05    0.010280
2020-05-10    0.017408
2020-05-24    0.017664
2020-06-07    0.017915
2020-06-21    0.015692
dtype: float64, 'total_secs': date
2019-10-06    3.195034e+06
2019-11-10    6.298366e+06
2019-12-08    3.988174e+06
2020-01-05    8.529607e+04
2020-02-09    2.300364e+06
2020-03-08    4.384130e+06
2020-04-05    3.725444e+06
2020-05-10    4.533269e+06
2020-05-24    7.292537e+04
2020-06-07    5.197466e+06
2020-06-21    1.231909e-02
dtype: float64, 'num_100': date
2019-10-06    0.002222
2019-11-10    0.008036
2019-12-08    0.008603
2020-01-05    0.013482
2020-02-09    0.018000
2020-03-08    0.015790
2020-04-05    0.018343
2020-05-10    0.015989
2020-05-24    0.015962
2020-06-07    0.023342
2020-06-21    0.020649
dtype: float64, 'num_985': date
2019-10-06    0.001328
2019-11-10    0.003673
2019-12-08    0.003685
2020-01-05    0.004147
2020-02-09    0.008472
2020-03-08    0.004797
2020-04-05    0.006440
2020-05-10    0.012172
2020-05-24    0.006589
2020-06-07    0.012551
2020-06-21    0.008751
dtype: float64, 'num_days': date
2019-10-06    0.015197
2019-11-10    0.020330
2019-12-08    0.020413
2020-01-05    0.021674
2020-02-09    0.027058
2020-03-08    0.027511
2020-04-05    0.032230
2020-05-10    0.035256
2020-05-24    0.033025
2020-06-07    0.027666
2020-06-21    0.036700
dtype: float64, 'registered_via': date
2019-10-06    0.030936
2019-11-10    0.023587
2019-12-08    0.035501
2020-01-05    0.036614
2020-02-09    0.033608
2020-03-08    0.048457
2020-04-05    0.044091
2020-05-10    0.040938
2020-05-24    0.047190
2020-06-07    0.045505
2020-06-21    0.038783
dtype: float64, 'days_listened': date
2019-10-06    0.029009
2019-11-10    0.056168
2019-12-08    0.069991
2020-01-05    0.094727
2020-02-09    0.114752
2020-03-08    0.123834
2020-04-05    0.138613
2020-05-10    0.140382
2020-05-24    0.143605
2020-06-07    0.148104
2020-06-21    0.150445
dtype: float64, 'is_auto_renew': date
2019-10-06    0.094599
2019-11-10    0.087026
2019-12-08    0.090617
2020-01-05    0.086463
2020-02-09    0.081688
2020-03-08    0.081942
2020-04-05    0.088144
2020-05-10    0.066405
2020-05-24    0.072674
2020-06-07    0.070106
2020-06-21    0.065089
dtype: float64, 'num_unq': date
2019-10-06    0.004557
2019-11-10    0.010202
2019-12-08    0.012707
2020-01-05    0.015691
2020-02-09    0.020453
2020-03-08    0.017341
2020-04-05    0.032700
2020-05-10    0.019344
2020-05-24    0.018512
2020-06-07    0.029853
2020-06-21    0.023184
dtype: float64, 'gender': date
2019-10-06    0.005762
2019-11-10    0.002788
2019-12-08    0.009743
2020-01-05    0.008910
2020-02-09    0.007340
2020-03-08    0.012474
2020-04-05    0.013840
2020-05-10    0.012628
2020-05-24    0.022039
2020-06-07    0.016379
2020-06-21    0.016094
dtype: float64, 'y_true49a0c676-35fd-11ea-978f-2e728ce88125': date
2019-10-06    0.003722
2019-11-10    0.002338
2019-12-08    0.003565
2020-01-05    0.003798
2020-02-09    0.004184
2020-03-08    0.004335
2020-04-05    0.005035
2020-05-10    0.002416
2020-05-24    0.002777
2020-06-07    0.002433
2020-06-21    0.002197
dtype: float64, 'is_cancel': date
2019-10-06    0.026147
2019-11-10    0.025565
2019-12-08    0.027264
2020-01-05    0.025866
2020-02-09    0.026749
2020-03-08    0.027748
2020-04-05    0.026637
2020-05-10    0.0

### Leakage

#### Index Train-Validation Leakage

In [24]:
index_train_validation_leakage(train_df_synthetic_leakage, val_df_synthetic_leakage)

0.4

In [25]:
index_train_validation_leakage(ds_train, ds_val)

0

#### Data Sample Leakage

In [41]:
data_sample_leakage_report(val_ds_index_leakage, train_ds_index_leakage)


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


12.0

In [ ]:
# data_sample_leakage_report(ds_val, ds_train)

### Performance

#### Classification Report

In [81]:
cls_report_check = ClassificationReport()

In [82]:
cls_report_check.run(ds_val, lending_club_model)

{0: {'precision': 0.37931153362177444, 'recall': 0.6671214188267395, 'f_score': 0.4836370030110553, 'support': 32985.0}, 1: {'precision': 0.8335758457620953, 'recall': 0.6043250846116655, 'f_score': 0.7006752452541726, 'support': 91004.0}}